# Stack Exchange

SE API: https://api.stackexchange.com/docs

Share dataset on HF Hub:
- https://huggingface.co/docs/datasets/en/create_dataset
- Advanced: https://huggingface.co/docs/datasets/main/en/dataset_script
- https://huggingface.co/docs/datasets/en/upload_dataset
    - Example dataset card: https://huggingface.co/datasets/cnn_dailymail
    - Getting started: https://huggingface.co/welcome

In [1]:
%load_ext autoreload
%autoreload 2

In [39]:
from requests import Session
import urllib.parse
from time import sleep
import pandas as pd
import os
import json

In [44]:
# Directory to store the data files
dest_dir = '/Users/ag2435/repos/stackexchange/'

In [3]:
BASE_URL = 'https://api.stackexchange.com/'
APPLICATION_KEY = ')KIPKiGfEARDVrtTHF2UKw(('
MAX_PAGESIZE = 100

In [4]:
def all(func):
    def wrapper(session, **kwargs):
        # get page from params or default to 1
        page = kwargs.get('page', 1)
        n_requests = 0

        while True:
            # add access token to unlock higher request quota
            if 'key' not in kwargs: kwargs['key'] = APPLICATION_KEY
            # use max page size to reduce number of requests
            if 'pagesize' not in kwargs: kwargs['pagesize'] = MAX_PAGESIZE
            # add page number to params
            kwargs['page'] = page

            response = func(session, **kwargs)
            # print('response', response)
            for el in response['items']:
                yield el
            # print(response.keys())
            # check if there are more pages
            print(f"page {page}: has_more={response['has_more']}, quota_remaining={response['quota_remaining']}/{response['quota_max']}")
            if 'has_more' in response and not response['has_more']:
                break
            page += 1

            if n_requests % 4 == 0:
                sleep(1)
    return wrapper

### Sites

TODO: get usage statistics for each site

In [5]:
@all
def get_sites(session, **kwargs):
    url = urllib.parse.urljoin(BASE_URL, '/2.3/sites')
    response = session.get(url, params=kwargs)
    return response.json()

In [6]:
with Session() as session:
    sites = list(get_sites(session))

page 1: has_more=True, quota_remaining=9951/10000
page 2: has_more=True, quota_remaining=9950/10000
page 3: has_more=True, quota_remaining=9949/10000
page 4: has_more=False, quota_remaining=9948/10000


In [7]:
sites[0]

{'aliases': ['https://www.stackoverflow.com',
  'https://facebook.stackoverflow.com'],
 'styling': {'tag_background_color': '#E0EAF1',
  'tag_foreground_color': '#3E6D8E',
  'link_color': '#0077CC'},
 'related_sites': [{'relation': 'meta',
   'api_site_parameter': 'meta.stackoverflow',
   'site_url': 'https://meta.stackoverflow.com',
   'name': 'Meta Stack Overflow'},
  {'relation': 'chat',
   'site_url': 'https://chat.stackoverflow.com/',
   'name': 'Stack Overflow Chat'}],
 'markdown_extensions': ['Prettify'],
 'launch_date': 1221436800,
 'open_beta_date': 1217462400,
 'site_state': 'normal',
 'high_resolution_icon_url': 'https://cdn.sstatic.net/Sites/stackoverflow/Img/apple-touch-icon@2.png',
 'favicon_url': 'https://cdn.sstatic.net/Sites/stackoverflow/Img/favicon.ico',
 'icon_url': 'https://cdn.sstatic.net/Sites/stackoverflow/Img/apple-touch-icon.png',
 'audience': 'professional and enthusiast programmers',
 'site_url': 'https://stackoverflow.com',
 'api_site_parameter': 'stackover

In [8]:
# SITE_KEYS = list(sites[0].keys())
SITE_KEYS = [
    'aliases', # exclude aliases key
    'styling',
    'related_sites',
    'markdown_extensions',
    'launch_date',
    'open_beta_date',
    'site_state',
    'high_resolution_icon_url',
    'favicon_url',
    'icon_url',
    'audience',
    'site_url',
    'api_site_parameter',
    'logo_url',
    'name',
    'site_type'
]

In [34]:
for i, site in enumerate(sites):
    print(i, site['site_url'], site['name'], site['api_site_parameter'], site['site_type'])

0 https://stackoverflow.com Stack Overflow stackoverflow main_site
1 https://serverfault.com Server Fault serverfault main_site
2 https://superuser.com Super User superuser main_site
3 https://meta.stackexchange.com Meta Stack Exchange meta main_site
4 https://webapps.stackexchange.com Web Applications webapps main_site
5 https://webapps.meta.stackexchange.com Web Applications Meta webapps.meta meta_site
6 https://gaming.stackexchange.com Arqade gaming main_site
7 https://gaming.meta.stackexchange.com Arqade Meta gaming.meta meta_site
8 https://webmasters.stackexchange.com Webmasters webmasters main_site
9 https://webmasters.meta.stackexchange.com Webmasters Meta webmasters.meta meta_site
10 https://cooking.stackexchange.com Seasoned Advice cooking main_site
11 https://cooking.meta.stackexchange.com Seasoned Advice Meta cooking.meta meta_site
12 https://gamedev.stackexchange.com Game Development gamedev main_site
13 https://gamedev.meta.stackexchange.com Game Development Meta gamedev.m

In [12]:
# # save to excel
# df = pd.DataFrame(sites)
# df = df[SITE_KEYS]
# df.to_excel('se_sites.xlsx', index=False)

### Advanced search

In [15]:
@all
def get_search_advanced(session, **kwargs):
    # Make a GET request
    # response = session.get('https://www.google.com')
    # # Print the status code of the response
    # print(response.status_code)

    # Convert the following to a GET request:
    # https://api.stackexchange.com/2.3/search/advanced?order=desc&sort=activity&body=arxiv&site=stackoverflow

    url = urllib.parse.urljoin(BASE_URL, '/2.3/search/advanced')
    response = session.get(url, params=kwargs)
    return response.json()

In [16]:
with Session() as session:
    params = {
        'order': 'desc',
        'sort': 'activity',
        'body': 'arxiv',
        'site': 'stackoverflow',
    }
    results = list(get_search_advanced(session, **params))

page 1: has_more=True, quota_remaining=9947/10000
page 2: has_more=False, quota_remaining=9946/10000


In [17]:
len(results)

148

In [22]:
results

[{'tags': ['python', 'keras', 'loss-function'],
  'owner': {'account_id': 30887162,
   'reputation': 1,
   'user_id': 23705688,
   'user_type': 'registered',
   'profile_image': 'https://www.gravatar.com/avatar/0fc28f4b92f679e46ac0a2013e5d1c45?s=256&d=identicon&r=PG&f=y&so-version=2',
   'display_name': 'Gst',
   'link': 'https://stackoverflow.com/users/23705688/gst'},
  'is_answered': False,
  'view_count': 20,
  'answer_count': 0,
  'score': -3,
  'last_activity_date': 1712064071,
  'creation_date': 1712062420,
  'last_edit_date': 1712064071,
  'question_id': 78261447,
  'content_license': 'CC BY-SA 4.0',
  'link': 'https://stackoverflow.com/questions/78261447/custom-loss-function-using-keras',
  'title': 'Custom loss function using keras'},
 {'tags': ['latex', 'submission'],
  'owner': {'account_id': 20425863,
   'reputation': 61,
   'user_id': 14985883,
   'user_type': 'registered',
   'profile_image': 'https://www.gravatar.com/avatar/d43029b34aa6ce285abf1b144a3db801?s=256&d=identi

## Construct dataset

We want to find all questions whose answers contain arXiv links.

In [46]:
with Session() as session:

    for site in ['stackoverflow',]:
        params = {
            'order': 'desc',
            'sort': 'activity',
            'body': 'arxiv',
            'site': site,
        }

        save_path = os.path.join(dest_dir, site)
        os.makedirs(save_path, exist_ok=True)
        print(f"Saving to {save_path}")
        
        results = list(get_search_advanced(session, **params))
        # save results to json
        file_path = os.path.join(save_path, 'val.json')
        print(file_path)
        with open(file_path, 'w') as f:
            json.dump(results, f, indent=2)

Saving to /Users/ag2435/repos/stackexchange/stackoverflow
page 1: has_more=True, quota_remaining=9931/10000
page 2: has_more=False, quota_remaining=9930/10000
/Users/ag2435/repos/stackexchange/stackoverflow/val.json
